In [1]:
# Мы всегда начинаем с набора данных для тренировки. Давайте загрузим крошечный набор данных по Шекспиру
!wget https://raw.githubusercontent.com/karpathy/char-rnn/master/data/tinyshakespeare/input.txt

--2025-07-18 04:57:04--  https://raw.githubusercontent.com/karpathy/char-rnn/master/data/tinyshakespeare/input.txt
Распознаётся raw.githubusercontent.com (raw.githubusercontent.com)… 185.199.109.133, 185.199.110.133, 185.199.111.133, ...
Подключение к raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... соединение установлено.
HTTP-запрос отправлен. Ожидание ответа… 200 OK
Длина: 1115394 (1,1M) [text/plain]
Сохранение в: «input.txt»

input.txt           100%[===================>]   1,06M  2,40MB/s    за 0,4s    

2025-07-18 04:57:05 (2,40 MB/s) - «input.txt» сохранён [1115394/1115394]



In [4]:
with open("input.txt",encoding='utf-8') as f:
    text = f.read()

In [5]:
text

"First Citizen:\nBefore we proceed any further, hear me speak.\n\nAll:\nSpeak, speak.\n\nFirst Citizen:\nYou are all resolved rather to die than to famish?\n\nAll:\nResolved. resolved.\n\nFirst Citizen:\nFirst, you know Caius Marcius is chief enemy to the people.\n\nAll:\nWe know't, we know't.\n\nFirst Citizen:\nLet us kill him, and we'll have corn at our own price.\nIs't a verdict?\n\nAll:\nNo more talking on't; let it be done: away, away!\n\nSecond Citizen:\nOne word, good citizens.\n\nFirst Citizen:\nWe are accounted poor citizens, the patricians good.\nWhat authority surfeits on would relieve us: if they\nwould yield us but the superfluity, while it were\nwholesome, we might guess they relieved us humanely;\nbut they think we are too dear: the leanness that\nafflicts us, the object of our misery, is as an\ninventory to particularise their abundance; our\nsufferance is a gain to them Let us revenge this with\nour pikes, ere we become rakes: for the gods know I\nspeak this in hunger 

In [6]:
print("Длина датаеста в символах: ", len(text))

Длина датаеста в символах:  1115394


In [7]:
# let's look at the first 1000 characters
print(text[:1000])

First Citizen:
Before we proceed any further, hear me speak.

All:
Speak, speak.

First Citizen:
You are all resolved rather to die than to famish?

All:
Resolved. resolved.

First Citizen:
First, you know Caius Marcius is chief enemy to the people.

All:
We know't, we know't.

First Citizen:
Let us kill him, and we'll have corn at our own price.
Is't a verdict?

All:
No more talking on't; let it be done: away, away!

Second Citizen:
One word, good citizens.

First Citizen:
We are accounted poor citizens, the patricians good.
What authority surfeits on would relieve us: if they
would yield us but the superfluity, while it were
wholesome, we might guess they relieved us humanely;
but they think we are too dear: the leanness that
afflicts us, the object of our misery, is as an
inventory to particularise their abundance; our
sufferance is a gain to them Let us revenge this with
our pikes, ere we become rakes: for the gods know I
speak this in hunger for bread, not in thirst for revenge.



In [13]:
chars = sorted(list(set(text)))
vocab_size = len(chars)
print(chars)
print(f"len: {vocab_size}")

['\n', ' ', '!', '$', '&', "'", ',', '-', '.', '3', ':', ';', '?', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']
len: 65


In [92]:
print(chars)

['\n', ' ', '!', '$', '&', "'", ',', '-', '.', '3', ':', ';', '?', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [16]:
# create a mapping from characters to integers
# string to integer
stoi = { ch:i for i,ch in enumerate(chars) }
## integer to string
itos = { i:ch for i,ch in enumerate(chars) }

encode = lambda s: [stoi[c] for c in s] # кодировщик: берем строку, выводим список целых чисел
decode = lambda l: ''.join([itos[i] for i in l]) #декодер: берем список целых чисел, выводим строку

print(encode("hii there"))
print(decode(encode("hii there")))

[46, 47, 47, 1, 58, 46, 43, 56, 43]
hii there


In [58]:
import torch
device = 'cuda' if torch.cuda.is_available() else 'cpu'

In [18]:
data = torch.tensor(encode(text),dtype=torch.long)

In [19]:
print(data.shape, data.dtype)
print(data[:1000]) # 1000 символов, которые мы просмотрели ранее, в GPT будут выглядеть следующим образомs

torch.Size([1115394]) torch.int64
tensor([18, 47, 56, 57, 58,  1, 15, 47, 58, 47, 64, 43, 52, 10,  0, 14, 43, 44,
        53, 56, 43,  1, 61, 43,  1, 54, 56, 53, 41, 43, 43, 42,  1, 39, 52, 63,
         1, 44, 59, 56, 58, 46, 43, 56,  6,  1, 46, 43, 39, 56,  1, 51, 43,  1,
        57, 54, 43, 39, 49,  8,  0,  0, 13, 50, 50, 10,  0, 31, 54, 43, 39, 49,
         6,  1, 57, 54, 43, 39, 49,  8,  0,  0, 18, 47, 56, 57, 58,  1, 15, 47,
        58, 47, 64, 43, 52, 10,  0, 37, 53, 59,  1, 39, 56, 43,  1, 39, 50, 50,
         1, 56, 43, 57, 53, 50, 60, 43, 42,  1, 56, 39, 58, 46, 43, 56,  1, 58,
        53,  1, 42, 47, 43,  1, 58, 46, 39, 52,  1, 58, 53,  1, 44, 39, 51, 47,
        57, 46, 12,  0,  0, 13, 50, 50, 10,  0, 30, 43, 57, 53, 50, 60, 43, 42,
         8,  1, 56, 43, 57, 53, 50, 60, 43, 42,  8,  0,  0, 18, 47, 56, 57, 58,
         1, 15, 47, 58, 47, 64, 43, 52, 10,  0, 18, 47, 56, 57, 58,  6,  1, 63,
        53, 59,  1, 49, 52, 53, 61,  1, 15, 39, 47, 59, 57,  1, 25, 39, 56, 41,
      

In [21]:
# Давайте теперь разделим данные на обучающие и проверочные наборы
n = int(0.9 * len(data))

train_data = data[:n]
val_data = data[n:]

In [22]:
block_size = 8
train_data[:block_size+1]

tensor([18, 47, 56, 57, 58,  1, 15, 47, 58])

In [25]:
x = train_data[:block_size]
y = train_data[1:block_size + 1]

for t in range(block_size):

    contex = x[:t + 1]
    target = y[t]

    print(f"когда на входе {contex} выход вот такой: {target}")

когда на входе tensor([18]) выход вот такой: 47
когда на входе tensor([18, 47]) выход вот такой: 56
когда на входе tensor([18, 47, 56]) выход вот такой: 57
когда на входе tensor([18, 47, 56, 57]) выход вот такой: 58
когда на входе tensor([18, 47, 56, 57, 58]) выход вот такой: 1
когда на входе tensor([18, 47, 56, 57, 58,  1]) выход вот такой: 15
когда на входе tensor([18, 47, 56, 57, 58,  1, 15]) выход вот такой: 47
когда на входе tensor([18, 47, 56, 57, 58,  1, 15, 47]) выход вот такой: 58


In [59]:
torch.manual_seed(1337)
batch_size = 4 #  сколько независимых последовательностей мы будем обрабатывать параллельно?
block_size = 8 # какова максимальная длина контекста для предсказаний?


# data loading
def get_batch(split):
    # generate a small batch of data of inputs x and targets y
    data = train_data if split == 'train' else val_data
    ix = torch.randint(len(data) - block_size, (batch_size,))
    x = torch.stack([data[i:i+block_size] for i in ix])
    y = torch.stack([data[i+1:i+block_size+1] for i in ix])
    x, y = x.to(device), y.to(device)
    return x, y

xb, yb = get_batch('train')
print('inputs:')
print(xb.shape)
print(xb)
print('targets:')
print(yb.shape)
print(yb)

print('----')



inputs:
torch.Size([4, 8])
tensor([[24, 43, 58,  5, 57,  1, 46, 43],
        [44, 53, 56,  1, 58, 46, 39, 58],
        [52, 58,  1, 58, 46, 39, 58,  1],
        [25, 17, 27, 10,  0, 21,  1, 54]])
targets:
torch.Size([4, 8])
tensor([[43, 58,  5, 57,  1, 46, 43, 39],
        [53, 56,  1, 58, 46, 39, 58,  1],
        [58,  1, 58, 46, 39, 58,  1, 46],
        [17, 27, 10,  0, 21,  1, 54, 39]])
----


In [32]:
for b in range(batch_size):

    for t in range(block_size):

        context = xb[b, :t+1]
        target = yb[b,t]

        print(f"когда на входе {context} выход вот такой: {target}")

        

когда на входе tensor([24]) выход вот такой: 43
когда на входе tensor([24, 43]) выход вот такой: 58
когда на входе tensor([24, 43, 58]) выход вот такой: 5
когда на входе tensor([24, 43, 58,  5]) выход вот такой: 57
когда на входе tensor([24, 43, 58,  5, 57]) выход вот такой: 1
когда на входе tensor([24, 43, 58,  5, 57,  1]) выход вот такой: 46
когда на входе tensor([24, 43, 58,  5, 57,  1, 46]) выход вот такой: 43
когда на входе tensor([24, 43, 58,  5, 57,  1, 46, 43]) выход вот такой: 39
когда на входе tensor([44]) выход вот такой: 53
когда на входе tensor([44, 53]) выход вот такой: 56
когда на входе tensor([44, 53, 56]) выход вот такой: 1
когда на входе tensor([44, 53, 56,  1]) выход вот такой: 58
когда на входе tensor([44, 53, 56,  1, 58]) выход вот такой: 46
когда на входе tensor([44, 53, 56,  1, 58, 46]) выход вот такой: 39
когда на входе tensor([44, 53, 56,  1, 58, 46, 39]) выход вот такой: 58
когда на входе tensor([44, 53, 56,  1, 58, 46, 39, 58]) выход вот такой: 1
когда на вхо

In [33]:
print(xb) # вход нашего трансформера

tensor([[24, 43, 58,  5, 57,  1, 46, 43],
        [44, 53, 56,  1, 58, 46, 39, 58],
        [52, 58,  1, 58, 46, 39, 58,  1],
        [25, 17, 27, 10,  0, 21,  1, 54]])


In [38]:
xb.shape

torch.Size([4, 8])

In [ ]:
import torch
import torch.nn as nn
from torch.nn import functional as F
torch.manual_seed(1337)


class BigramLanguageModel(nn.Module):

    def __init__(self, vocab_size):
        super().__init__()
        # каждый токен напрямую считывает логиты для следующего токена из таблицы поиска
        self.token_embedding_table = nn.Embedding(vocab_size, vocab_size)

        ## по сути ембединг каждого вектора 65

    def forward(self, idx, targets=None):

        # idx and targets are both (B,T) tensor of integers (тут умножаем на матрицу эмбедингов)
        logits = self.token_embedding_table(idx) #torch.Size([batch_size, block_size, embeding_size])

       
        if targets is None:
            loss = None
        else:
            # [batch_size, block_size, embeding_size]
            B, T, C = logits.shape

            logits = logits.view(B*T, C)
            targets = targets.view(B*T)
            loss = F.cross_entropy(logits, targets)

        return logits, loss
    

    def generate(self, idx, max_new_tokens):
        # idx is (B, T) array of indices in the current context
        for _ in range(max_new_tokens):
            # get the predictions
            logits, loss = self(idx)
            # focus only on the last time step
            logits = logits[:, -1, :] # becomes (B, C)
            # apply softmax to get probabilities
            probs = F.softmax(logits, dim=-1) # (B, C)
            # sample from the distribution
            idx_next = torch.multinomial(probs, num_samples=1) # (B, 1)
            # append sampled index to the running sequence
            idx = torch.cat((idx, idx_next), dim=1) # (B, T+1)
        return idx
    


m = BigramLanguageModel(vocab_size)
logits, loss = m(xb, yb)
print(logits.shape)
print(loss)

print(decode(m.generate(idx = torch.zeros((1, 1), dtype=torch.long), max_new_tokens=100)[0].tolist()))



torch.Size([32, 65])
tensor(4.8786, grad_fn=<NllLossBackward0>)

SKIcLT;AcELMoTbvZv C?nq-QE33:CJqkOKH-q;:la!oiywkHjgChzbQ?u!3bLIgwevmyFJGUGp
wnYWmnxKWWev-tDqXErVKLgJ


In [40]:
# создаем a PyTorch optimizer
optimizer = torch.optim.AdamW(m.parameters(), lr=1e-3)

In [49]:
batch_size = 32

for step in range(100000):

    xb, yb = get_batch("train")

    logits, loss = m(xb, yb)
    optimizer.zero_grad(set_to_none=True)

    loss.backward()
    optimizer.step()

    print(f"STEP: {step} loss: {loss.item()}")

STEP: 0 loss: 2.9154887199401855
STEP: 1 loss: 2.7992191314697266
STEP: 2 loss: 2.86185622215271
STEP: 3 loss: 2.9399003982543945
STEP: 4 loss: 2.6853713989257812
STEP: 5 loss: 2.8295867443084717
STEP: 6 loss: 2.7676808834075928
STEP: 7 loss: 2.8483238220214844
STEP: 8 loss: 2.736626148223877
STEP: 9 loss: 2.7042665481567383
STEP: 10 loss: 2.7670886516571045
STEP: 11 loss: 2.7584009170532227
STEP: 12 loss: 2.7523646354675293
STEP: 13 loss: 2.7970938682556152
STEP: 14 loss: 2.765761613845825
STEP: 15 loss: 2.8704917430877686
STEP: 16 loss: 2.79677414894104
STEP: 17 loss: 2.6361281871795654
STEP: 18 loss: 2.692230224609375
STEP: 19 loss: 2.776977777481079
STEP: 20 loss: 2.8378162384033203
STEP: 21 loss: 2.798584461212158
STEP: 22 loss: 2.8082985877990723
STEP: 23 loss: 2.6807491779327393
STEP: 24 loss: 2.8751680850982666
STEP: 25 loss: 2.7750930786132812
STEP: 26 loss: 2.8104209899902344
STEP: 27 loss: 2.7774133682250977
STEP: 28 loss: 2.8528671264648438
STEP: 29 loss: 2.8163371086120605

In [57]:

input_str = "hello"

inpute_emb = encode(input_str)
print(inpute_emb)
print(decode(m.generate(idx = torch.tensor([inpute_emb], dtype=torch.long), max_new_tokens=500)[0].tolist()))

[46, 43, 50, 50, 53]
hellove.
Shy abee Vowieyoroye y mo awilloouivel and bay buly'lditharelyo; this hand
isthoxin.
Coues maucawith d toucimercthary.
Bou y marere g Juinoupl tho if oper d; h ous iotou LESI tougene puand, mine acoodend tsthitil
CAgong, beanso POMIORIme be Bye: ICownt s, Yot y hod?
PUMICatwhay ld g.
Wen, ouct at franr:

NThe
Won bay t arawenotheave HEThe.
RS:
OFinh adis an ouls y r y ss;
NGorvery'tlon ll
TI

MEd
GRO: trttherandwneses isoa s,
AUS: bumerupead hivemaponarere, mongrmehon th,-ff oo fon s l,
D IA


## The mathematical trick in self-attention

In [63]:
torch.manual_seed(1337)

B, T, C = 4, 8, 2 

x = torch.randn(B, T , C)
x.shape

torch.Size([4, 8, 2])

In [ ]:
# We want x[b,t] = mean_{i<=t} x[b,i] берем среднее до
xbow = torch.zeros((B,T,C))
for b in range(B):
    for t in range(T):
        xprev = x[b,:t+1] # (t,C)
        xbow[b,t] = torch.mean(xprev, 0)

In [65]:
x[0]

tensor([[ 0.1808, -0.0700],
        [-0.3596, -0.9152],
        [ 0.6258,  0.0255],
        [ 0.9545,  0.0643],
        [ 0.3612,  1.1679],
        [-1.3499, -0.5102],
        [ 0.2360, -0.2398],
        [-0.9211,  1.5433]])

In [66]:
xbow[0]

tensor([[ 0.1808, -0.0700],
        [-0.0894, -0.4926],
        [ 0.1490, -0.3199],
        [ 0.3504, -0.2238],
        [ 0.3525,  0.0545],
        [ 0.0688, -0.0396],
        [ 0.0927, -0.0682],
        [-0.0341,  0.1332]])

In [68]:
a = torch.tril(torch.ones(3, 3))
a

tensor([[1., 0., 0.],
        [1., 1., 0.],
        [1., 1., 1.]])

In [ ]:
# toy example illustrating how matrix multiplication can be used for a "weighted aggregation"
torch.manual_seed(42)
a = torch.tril(torch.ones(3, 3)) ## треугольная матрица для векторов
a = a / torch.sum(a, 1, keepdim=True)  ## делаем чтоьы сумма была 1
b = torch.randint(0,10,(3,2)).float()
c = a @ b
print('a=')
print(a)
print('--')
print('b=')
print(b)
print('--')
print('c=')
print(c)

a=
tensor([[1.0000, 0.0000, 0.0000],
        [0.5000, 0.5000, 0.0000],
        [0.3333, 0.3333, 0.3333]])
--
b=
tensor([[2., 7.],
        [6., 4.],
        [6., 5.]])
--
c=
tensor([[2.0000, 7.0000],
        [4.0000, 5.5000],
        [4.6667, 5.3333]])


In [70]:
## новые веса

# version 2: using matrix multiply for a weighted aggregation
wei = torch.tril(torch.ones(T, T))
wei = wei / wei.sum(1, keepdim=True)
xbow2 = wei @ x # (B, T, T) @ (B, T, C) ----> (B, T, C)
torch.allclose(xbow, xbow2) ## сравнение предыдушего подхода

True

In [71]:
tril = torch.tril(torch.ones(T, T))
tril

tensor([[1., 0., 0., 0., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0., 0., 0., 0.],
        [1., 1., 1., 0., 0., 0., 0., 0.],
        [1., 1., 1., 1., 0., 0., 0., 0.],
        [1., 1., 1., 1., 1., 0., 0., 0.],
        [1., 1., 1., 1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1., 1., 1., 1.]])

In [72]:
wei = torch.zeros((T,T))
wei

tensor([[0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0., 0.]])

In [73]:
wei = wei.masked_fill(tril == 0, float('-inf'))
wei

tensor([[0., -inf, -inf, -inf, -inf, -inf, -inf, -inf],
        [0., 0., -inf, -inf, -inf, -inf, -inf, -inf],
        [0., 0., 0., -inf, -inf, -inf, -inf, -inf],
        [0., 0., 0., 0., -inf, -inf, -inf, -inf],
        [0., 0., 0., 0., 0., -inf, -inf, -inf],
        [0., 0., 0., 0., 0., 0., -inf, -inf],
        [0., 0., 0., 0., 0., 0., 0., -inf],
        [0., 0., 0., 0., 0., 0., 0., 0.]])

In [74]:
wei = F.softmax(wei, dim=-1)
wei

tensor([[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.5000, 0.5000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.3333, 0.3333, 0.3333, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.2500, 0.2500, 0.2500, 0.2500, 0.0000, 0.0000, 0.0000, 0.0000],
        [0.2000, 0.2000, 0.2000, 0.2000, 0.2000, 0.0000, 0.0000, 0.0000],
        [0.1667, 0.1667, 0.1667, 0.1667, 0.1667, 0.1667, 0.0000, 0.0000],
        [0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.1429, 0.0000],
        [0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250, 0.1250]])

In [75]:
xbow3 = wei @ x
xbow3

tensor([[[ 0.1808, -0.0700],
         [-0.0894, -0.4926],
         [ 0.1490, -0.3199],
         [ 0.3504, -0.2238],
         [ 0.3525,  0.0545],
         [ 0.0688, -0.0396],
         [ 0.0927, -0.0682],
         [-0.0341,  0.1332]],

        [[ 1.3488, -0.1396],
         [ 0.8173,  0.4127],
         [-0.1342,  0.4395],
         [ 0.2711,  0.4774],
         [ 0.2421,  0.0694],
         [ 0.0084,  0.0020],
         [ 0.0712, -0.1128],
         [ 0.2527,  0.2149]],

        [[-0.6631, -0.2513],
         [ 0.1735, -0.0649],
         [ 0.1685,  0.3348],
         [-0.1621,  0.1765],
         [-0.2312, -0.0436],
         [-0.1015, -0.2855],
         [-0.2593, -0.1630],
         [-0.3015, -0.2293]],

        [[ 1.6455, -0.8030],
         [ 1.4985, -0.5395],
         [ 0.4954,  0.3420],
         [ 1.0623, -0.1802],
         [ 1.1401, -0.4462],
         [ 1.0870, -0.4071],
         [ 1.0430, -0.1299],
         [ 1.1138, -0.1641]]])

In [76]:
# version 3: use Softmax
tril = torch.tril(torch.ones(T, T))
wei = torch.zeros((T,T))
wei = wei.masked_fill(tril == 0, float('-inf'))
wei = F.softmax(wei, dim=-1)
xbow3 = wei @ x
torch.allclose(xbow, xbow3)

True

In [83]:
# version 4: self-attention!
torch.manual_seed(1337)
B,T,C = 4,8,32 # batch, time, channels
x = torch.randn(B,T,C)


head_size = 16

key = nn.Linear(C, head_size, bias=False)
query = nn.Linear(C, head_size, bias=False)
value = nn.Linear(C, head_size, bias=False)

k = key(x)# (B, T, 16)
q = query(x)# (B, T, 16)

wei = q @ k.transpose(-2, -1) # (B, T, 16) @ (B, 16, T) ---> (B, T, T)

tril = torch.tril(torch.ones(T, T))
#wei = torch.zeros((T, T))
wei = wei.masked_fill(tril==0, float("-inf"))
wei = F.softmax(wei, dim=-1)

v = value(x)

out = wei @ v
#out = wei @ x
print(wei)
out.shape

tensor([[[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.1574, 0.8426, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.2088, 0.1646, 0.6266, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.5792, 0.1187, 0.1889, 0.1131, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.0294, 0.1052, 0.0469, 0.0276, 0.7909, 0.0000, 0.0000, 0.0000],
         [0.0176, 0.2689, 0.0215, 0.0089, 0.6812, 0.0019, 0.0000, 0.0000],
         [0.1691, 0.4066, 0.0438, 0.0416, 0.1048, 0.2012, 0.0329, 0.0000],
         [0.0210, 0.0843, 0.0555, 0.2297, 0.0573, 0.0709, 0.2423, 0.2391]],

        [[1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.1687, 0.8313, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.2477, 0.0514, 0.7008, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.4410, 0.0957, 0.3747, 0.0887, 0.0000, 0.0000, 0.0000, 0.0000],
         [0.0069, 0.0456, 0.0300, 0.7748, 0.1427, 0.0000, 0.0000, 0.0000],
         [0.0660, 0.089

torch.Size([4, 8, 16])

Записи:
- Внимание - это ** механизм коммуникации **. Его можно рассматривать как узлы в ориентированном графе, которые смотрят друг на друга и объединяют информацию со взвешенной суммой из всех узлов, которые указывают на них, с весами, зависящими от данных.
- Здесь нет понятия пространства. Внимание просто воздействует на набор векторов. Вот почему нам нужно позиционно кодировать токены.
- Каждый пример в пакетном измерении, конечно, обрабатывается полностью независимо и никогда не "общается" друг с другом
- В блоке внимания "encoder" просто удалите единственную строку, которая маскирует "tril", позволяя всем токенам взаимодействовать. Этот блок здесь называется блоком внимания "декодер", потому что он имеет треугольную маскировку и обычно используется в настройках авторегрессии, таких как языковое моделирование.
- "саморегрессия" просто означает, что ключи и значения генерируются из того же источника, что и запросы. При "перекрестном внимании" запросы по-прежнему генерируются из x, но ключи и значения поступают из какого-либо другого внешнего источника (например, модуля кодирования).
- "Масштабируемое" внимание дополнительно делит "wei" на 1/кв.м(head_size). Таким образом, когда входные данные Q, K представляют собой единичную дисперсию, wei также будет единичной дисперсией, а Softmax останется рассеянным и не будет слишком насыщенным. Иллюстрация ниже

In [84]:
k = torch.randn(B,T,head_size)
q = torch.randn(B,T,head_size)
wei = q @ k.transpose(-2, -1) #* head_size**-0.5

In [86]:
print(k.var())
print(q.var())
print(wei.var())

tensor(1.0449)
tensor(1.0700)
tensor(17.4690)


In [87]:
k = torch.randn(B,T,head_size)
q = torch.randn(B,T,head_size)
wei = q @ k.transpose(-2, -1) * head_size**-0.5

In [88]:
print(k.var())
print(q.var())
print(wei.var())

tensor(0.9006)
tensor(1.0037)
tensor(0.9957)


In [89]:
torch.softmax(torch.tensor([0.1, -0.2, 0.3, -0.2, 0.5]), dim=-1)

tensor([0.1925, 0.1426, 0.2351, 0.1426, 0.2872])

In [90]:
torch.softmax(torch.tensor([0.1, -0.2, 0.3, -0.2, 0.5])*8, dim=-1) # gets too peaky, converges to one-hot

tensor([0.0326, 0.0030, 0.1615, 0.0030, 0.8000])

In [ ]:
class Head(nn.Module):

    def __init__(self,head_size, n_embed = 65):

        super().__init__()

        self.key = nn.Linear(n_embed, head_size, bias= False)
        self.query = nn.Linear(n_embed, head_size, bias=False)
        self.value = nn.Linear(n_embed, head_size, bias=False)

        self.register_buffer('tril', torch.tril(torch.ones(block_size, block_size)))
        self.dropout = nn.Dropout(0.0)

    def forward(self, x):
        B,T,C = x.shape # [batch_size, block_size, embeding_size]

        k = self.key(x)  # [batch_size, block_size, embeding_size]
        q = self.query(x)# [batch_size, block_size, embeding_size]
        v = self.value(x)# [batch_size, block_size, embeding_size]


        wei = q @ k.transpose(-2, -1) * C ** -0.5 # # (B, T, C) @ (B, C, T) -> (B, T, T)

        wei = wei.masked_fill(self.tril[:T, :T] == 0, float('-inf')) # (B, T, T)
        wei = F.softmax(wei, dim=-1) # (B, T, T)

        wei = self.dropout(wei)
        # perform the weighted aggregation of the values
        
        out = wei @ v # (B, T, T) @ (B, T, C) -> (B, T, C)
        return out

        